*Eduardus Tjitrahardja | @edutjie | 2022*

# Ristek Datathon 2022: Extract

## Importing Libraries

In [1]:
import pandas as pd
import numpy as np

import nltk
from tqdm import tqdm, notebook
from gensim.models.fasttext import load_facebook_model

from keras.applications.vgg19 import preprocess_input as vgg19_preprocess_input, VGG19
from keras.applications.densenet import preprocess_input as densenet_preprocess_input, DenseNet121
import keras.utils as image
from keras import layers
from keras.models import Model
import keras.backend as K

In [3]:
combined_df = pd.read_csv('dataset/processed_combined.csv')
combined_df.head()

created_at                   id  ...                media label
0  2020-02-23 04:06:39+00:00  1231430140824973313  ...  ERbrKgFU4AAnADb.jpg   0.0
1  2020-01-05 01:46:46+00:00  1213637932411580417  ...  ENe1HUVUEAANLFT.jpg   0.0
2  2020-01-18 06:22:09+00:00  1218418277946396673  ...  EOiw80RU0AcJ4CI.jpg   0.0
3  2020-02-22 23:38:00+00:00  1231362534717837313  ...  ERatrt9UYAAtLMI.jpg   0.0
4  2019-12-17 10:54:31+00:00  1206890412574568449  ...  EL-8Z-vUcAIiIlV.jpg   0.0

[5 rows x 8 columns]

In [4]:
train_df = combined_df[combined_df['label'].notnull()]
test_df = combined_df[combined_df['label'].isnull() & combined_df['media'].notnull()]
unlabeled_df = combined_df[combined_df['label'].isnull() & combined_df['media'].isnull()]

train_df.shape, test_df.shape, unlabeled_df.shape, combined_df.shape

((1518, 8), (1011, 8), (9936, 8), (12465, 8))

## Image Feature

In [2]:
# extract images features from media column using vgg19
def extract_features(df, model, preprocess_input):
    img_size = 256
    batch_size = 16
    n_batches = df.shape[0] // batch_size + 1
    features = {}
    for b in notebook.tqdm(range(n_batches)):
        start = b * batch_size
        end = (b + 1) * batch_size
        batch = df[start:end]
        images = []
        for image_path in batch["media"]:
            img = image.load_img(f"dataset/media/Image/{image_path}", target_size=(img_size, img_size))
            x = image.img_to_array(img)
            x = np.expand_dims(x, axis=0)
            x = preprocess_input(x)
            images.append(x)
        images = np.vstack(images)
        batch_features = model.predict(images)
        for i, index in enumerate(batch.index):
            features[index] = batch_features[i]
    return pd.DataFrame.from_dict(features, orient="index")

### VGG19

In [41]:
inp = layers.Input((256,256,3))
backbone = VGG19(weights='imagenet', include_top=False, input_tensor=inp)
x = backbone.output
x = layers.GlobalAveragePooling2D()(x)
x = layers.Lambda(lambda x: K.expand_dims(x,axis = -1))(x)
x = layers.AveragePooling1D(4)(x)
out = layers.Lambda(lambda x: x[:,:,0])(x)

vgg19_model = Model(inp,out)

In [47]:
train_df.media.nunique()

1517

In [50]:
features = extract_features(train_df, vgg19_model)
features.head()

  0%|          | 0/95 [00:00<?, ?it/s]

1/1 [==============================] - 0s 42ms/step


0         1         2         3         4         5         6    \
0  1.352288  1.014886  4.034522  1.031563  1.124940  3.010315  1.683836   
1  0.221165  1.658107  2.771854  0.703428  0.426010  1.664204  0.666496   
2  0.594882  0.389002  0.036172  0.690939  0.326817  0.175458  0.505132   
3  0.000000  0.895361  0.000000  0.651359  1.416523  0.107897  0.850757   
4  0.443059  1.767194  1.864106  0.997791  0.572493  2.994671  1.046537   

        7         8         9    ...       118       119       120       121  \
0  3.008744  2.046914  0.221159  ...  3.672439  0.474019  5.825624  3.236522   
1  3.533314  1.088824  0.427827  ...  2.604076  0.569781  6.766608  8.160769   
2  0.500877  2.187993  0.631999  ...  6.489656  0.766638  0.172080  0.646592   
3  0.260024  0.465739  0.678235  ...  0.531128  0.364114  1.135422  0.112131   
4  3.473873  1.164435  0.041928  ...  0.479829  1.308075  3.343970  5.646572   

        122       123       124       125       126       127  
0  1.618736  4.117425  1.665372  1.647556  6.883621  2.747848  
1  1.653374  0.417267  1.075007  1.685622  1.218619  9.190394  
2  0.048913  1.525172  0.504017  0.044370  1.049962  1.501683  
3  0.040652  6.959232  0.675484  0.198752  0.724027  0.399903  
4  0.818348  1.267661  0.796877  0.237935  0.379691  2.857185  

[5 rows x 128 columns]

In [53]:
features.to_csv('dataset/image_features/train_image_features.csv', index=False)

In [51]:
features.shape

(1518, 128)

In [56]:
test_image_features = extract_features(test_df, vgg19_model)
test_image_features.head()

  0%|          | 0/64 [00:00<?, ?it/s]

1/1 [==============================] - 0s 17ms/step


0         1         2         3         4         5         6    \
1518  0.187742  0.919194  0.536657  0.872991  0.699801  2.547535  1.368634   
1519  1.081535  0.343502  2.172968  3.097183  0.528741  3.390510  1.852074   
1520  0.594911  0.568306  2.661523  0.818910  1.096238  1.279988  3.859164   
1521  0.008054  2.782911  0.393933  1.575088  2.862458  0.536409  3.931819   
1522  0.032812  0.500018  1.095476  1.889700  1.660288  0.763369  1.849987   

           7         8         9    ...       118       119       120  \
1518  8.072812  1.832673  0.044823  ...  1.125442  1.634206  2.846357   
1519  6.226005  0.748891  0.453571  ...  3.770203  2.613887  1.067632   
1520  2.375810  0.347734  0.161990  ...  2.462411  0.690099  2.405854   
1521  6.853976  1.273635  0.000917  ...  0.703340  0.341360  4.508155   
1522  1.180393  0.106265  0.000000  ...  0.766487  0.190774  4.851637   

           121       122       123       124       125       126       127  
1518  5.086789  1.339693  4.428577  1.174664  3.413805  1.214123  3.468926  
1519  4.110927  1.913855  4.505924  0.618563  2.125443  3.565013  9.079924  
1520  2.778926  1.044922  1.572516  0.743471  1.847108  1.778436  4.328998  
1521  3.449048  0.313936  1.829808  0.160399  0.836640  1.102968  2.660489  
1522  2.176356  0.138018  0.460158  0.102598  1.459810  0.488602  4.208575  

[5 rows x 128 columns]

In [ ]:
test_image_features.to_csv('dataset/image_features/test_image_features.csv', index=False)

In [16]:
model = VGG19(weights='imagenet', include_top=False)
train_features = extract_features(train_df, model)

train_features

1/1 [==============================] - 0s 15ms/step


[array([[[[ 0.        ,  0.        ,  0.        , ...,  0.        ,
           17.842972  ,  0.        ],
          [ 0.        ,  0.        ,  0.        , ...,  0.        ,
           13.583393  ,  0.        ],
          [ 0.        ,  0.        ,  0.        , ...,  0.        ,
           13.533809  ,  0.        ],
          ...,
          [ 0.        ,  0.        ,  0.        , ...,  0.        ,
            0.        ,  0.        ],
          [ 0.        ,  0.        ,  0.        , ...,  0.        ,
            0.        ,  0.        ],
          [ 0.        ,  0.        ,  0.        , ...,  0.        ,
            4.5380044 ,  0.        ]],
 
         [[ 0.        ,  0.        ,  0.        , ...,  0.        ,
            9.064399  ,  0.        ],
          [ 0.        ,  0.        ,  0.        , ...,  0.        ,
           12.391933  ,  0.        ],
          [ 0.        ,  0.        ,  0.        , ...,  0.        ,
           18.707062  ,  0.        ],
          ...,
          [ 0

In [17]:
# store features in a npy file
np.save('dataset/image_features/train_img_features.npy', train_features)

In [33]:
# load features from npy file
train_features = np.load('dataset/image_features/train_img_features.npy')

In [27]:
# convert features to a dataframe
train_features = pd.DataFrame(train_features.reshape(train_features.shape[0], -1))
train_features.head()

0      1      2      3      4       5      6          7      8      9      \
0    0.0    0.0    0.0    0.0    0.0  0.0000    0.0   0.737864    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0  0.0000    0.0   0.000000    0.0    0.0   
2    0.0    0.0    0.0    0.0    0.0  0.0000    0.0   0.000000    0.0    0.0   
3    0.0    0.0    0.0    0.0    0.0  7.2044    0.0   0.000000    0.0    0.0   
4    0.0    0.0    0.0    0.0    0.0  0.0000    0.0  11.906753    0.0    0.0   

   ...      32758  32759     32760      32761  32762  32763      32764  32765  \
0  ...  23.985191    0.0  0.000000  10.401962    0.0    0.0  20.480049    0.0   
1  ...   0.000000    0.0  0.000000   0.000000    0.0    0.0   0.000000    0.0   
2  ...   0.000000    0.0  0.000000   0.000000    0.0    0.0   0.000000    0.0   
3  ...   6.726958    0.0  0.000000   0.000000    0.0    0.0   5.147472    0.0   
4  ...   0.000000    0.0  6.184856   0.000000    0.0    0.0   0.000000    0.0   

   32766  32767  
0    0.0    0.0  
1    0.0    0.0  
2    0.0    0.0  
3    0.0    0.0  
4    0.0    0.0  

[5 rows x 32768 columns]

### DenseNet

In [5]:
inp = layers.Input((256,256,3))
backbone = DenseNet121(input_tensor = inp, include_top = False)
x = backbone.output
x = layers.GlobalAveragePooling2D()(x)
x = layers.Lambda(lambda x: K.expand_dims(x,axis = -1))(x)
x = layers.AveragePooling1D(4)(x)
out = layers.Lambda(lambda x: x[:,:,0])(x)

densenet_model = Model(inp,out)

In [6]:
densenet_train_features = extract_features(train_df, densenet_model, densenet_preprocess_input)

  0%|          | 0/95 [00:00<?, ?it/s]

1/1 [==============================] - 1s 1s/step


In [7]:
densenet_train_features.head()

0         1         2    ...       253       254       255
0  0.002412  0.255406  0.073089  ...  0.933903  0.325151  0.782075
1  0.003262  0.209445  0.076465  ...  0.339387  1.417239  2.256201
2  0.001464  0.083154  0.018514  ...  0.214892  0.245031  0.456718
3  0.001842  0.070153  0.027252  ...  0.328360  0.129048  0.646415
4  0.003214  0.142908  0.028323  ...  0.283688  0.721310  1.036716

[5 rows x 256 columns]

In [8]:
densenet_train_features.shape

(1518, 256)

In [9]:
densenet_train_features.to_csv('dataset/image_features/densenet_train_image_features.csv', index=False)

In [10]:
densenet_test_features = extract_features(test_df, densenet_model, densenet_preprocess_input)
densenet_test_features.head()

  0%|          | 0/64 [00:00<?, ?it/s]

1/1 [==============================] - 1s 1s/step


0         1         2    ...       253       254       255
1518  0.004273  0.114928  0.039943  ...  0.343682  0.835717  1.247456
1519  0.003102  0.130681  0.054041  ...  0.914106  1.116877  1.509390
1520  0.002691  0.195683  0.083915  ...  1.613291  0.852301  0.932952
1521  0.003613  0.062647  0.027166  ...  0.842660  1.123443  0.740326
1522  0.003338  0.099204  0.039586  ...  0.441209  0.549615  0.989312

[5 rows x 256 columns]

In [11]:
densenet_test_features.to_csv('dataset/image_features/densenet_test_image_features.csv', index=False)

## Textual Feature

In [4]:
word_tokens = [nltk.tokenize.word_tokenize(i) for i in tqdm(train_df['text'])]
word_tokens[0]

100%|██████████| 1518/1518 [00:00<00:00, 4152.15it/s]


['akhir', 'juga', 'terobos', 'banjir']

In [5]:
ft_model = load_facebook_model('model/cc.id.300.bin')

In [14]:
ft_model.wv["banjir"]

array([-7.83165824e-03, -4.73202355e-02,  8.81230012e-02,  8.53706971e-02,
        1.34003013e-01, -2.88168043e-02, -1.50032043e-02, -1.28381401e-02,
        5.83951641e-03, -7.91077912e-02,  7.72436708e-02, -5.45463264e-02,
       -6.02833517e-02,  7.32105458e-03, -6.14437237e-02, -7.42493570e-02,
        2.84109712e-02, -6.95406869e-02, -2.40010023e-02,  9.62492451e-02,
        7.90210217e-02, -2.65017096e-02,  3.28898728e-02,  9.60502476e-02,
       -6.41337782e-02, -1.67172346e-02,  2.82737613e-02,  1.23081505e-02,
       -2.35787332e-02,  6.74109980e-02,  9.71845388e-02, -1.78277344e-02,
       -2.19146591e-02,  4.87571731e-02,  5.07424362e-02, -9.26893950e-03,
        4.04309183e-02, -2.18150970e-02,  1.14140436e-02,  4.27799486e-03,
        2.23270766e-02, -5.68529665e-02, -5.59097528e-02,  1.95064135e-02,
        5.14670499e-02, -4.36659344e-02, -5.62395975e-02, -7.81683326e-02,
        5.62892668e-02, -8.08358751e-03,  1.12346984e-01, -3.24015543e-02,
       -1.49580063e-02, -

In [12]:
ft_model.wv.most_similar('banjir', topn=10)

[('banjir-banjir', 0.8044018149375916),
 ('banjir.', 0.758131742477417),
 ('Banjir', 0.747555673122406),
 ('banjir3', 0.7226011157035828),
 ('banjirnya', 0.7184047102928162),
 ('bajir', 0.710436999797821),
 ('Banjir-banjir', 0.6992826461791992),
 ('pascabanjir', 0.6976428627967834),
 ('banjirpun', 0.6711414456367493),
 ('bandang', 0.6662591695785522)]

In [17]:
embedded_words = [[ft_model.wv[word] for word in token] for token in tqdm(word_tokens)]
embedded_words_encoding = [np.mean(embedded_word, axis=0) for embedded_word in tqdm(embedded_words)]
df_embedding = pd.DataFrame(embedded_words_encoding)
df_embedding.head()

100%|██████████| 1518/1518 [00:00<00:00, 41538.87it/s]


0         1         2         3         4         5         6    \
0  0.009883 -0.021286  0.025969  0.092511  0.028668 -0.028770  0.016315   
1  0.034512  0.009235  0.018049  0.045457  0.006226 -0.075077  0.004485   
2  0.037173 -0.050290  0.011853  0.118136 -0.018496 -0.046303  0.029109   
3  0.000976 -0.008979  0.025069  0.051203  0.021625 -0.046954  0.021365   
4  0.029130  0.045310  0.027381  0.040282 -0.047682  0.001377  0.017470   

        7         8         9    ...       290       291       292       293  \
0 -0.010510  0.008982 -0.090800  ...  0.007333  0.013171  0.015966 -0.002016   
1 -0.026857 -0.048104 -0.050542  ... -0.040443 -0.033196 -0.006029  0.014043   
2  0.011791 -0.015547 -0.080154  ... -0.032494 -0.030817 -0.034458  0.015121   
3  0.008321 -0.029315 -0.015738  ... -0.010753  0.018024 -0.011522 -0.014646   
4 -0.008542  0.011416 -0.097448  ... -0.014846 -0.011152 -0.055743  0.017050   

        294       295       296       297       298       299  
0  0.032844 -0.006217  0.022417 -0.057426  0.017508  0.033850  
1 -0.015839  0.013577  0.005713  0.001407 -0.003548  0.020258  
2 -0.031749  0.027591 -0.008889 -0.035597 -0.008871  0.061395  
3  0.006166  0.028416  0.047759  0.010205 -0.007385  0.051342  
4 -0.014798  0.048946  0.032517 -0.016963 -0.012313  0.021128  

[5 rows x 300 columns]

In [19]:
def embedding(df, model):
    word_tokens = [nltk.tokenize.word_tokenize(i) for i in tqdm(df['text'])]
    embedded_words = [[model.wv[word] for word in token] for token in tqdm(word_tokens)]
    embedded_words_encoding = [np.mean(embedded_word, axis=0) for embedded_word in tqdm(embedded_words)]
    df_embedding = pd.DataFrame(embedded_words_encoding)
    return df_embedding

In [20]:
test_df_embedding = embedding(test_df, ft_model)
unlabeled_df_embedding = embedding(unlabeled_df, ft_model)

100%|██████████| 9936/9936 [00:00<00:00, 45980.75it/s]


In [22]:
# export to csv
df_embedding.to_csv('dataset/text_features/train_text_features.csv', index=False)
test_df_embedding.to_csv('dataset/text_features/test_text_features.csv', index=False)
unlabeled_df_embedding.to_csv('dataset/text_features/unlabeled_text_features.csv', index=False)

In [36]:
df_embedding = pd.read_csv('dataset/text_features/train_text_features.csv')
test_df_embedding = pd.read_csv('dataset/text_features/test_text_features.csv')
unlabeled_df_embedding = pd.read_csv('dataset/text_features/unlabeled_text_features.csv')

df_embedding.shape, test_df_embedding.shape, unlabeled_df_embedding.shape

((1518, 300), (1011, 300), (9936, 300))